This is work in progress.

In [3]:
import sys
sys.path.insert(0, '..')
import cProfile
import numpy as np; print('numpy', np.__version__)
import zarr; print('zarr', 'refactor', 'blosc', ' '.join(zarr.blosc.version()))
import bcolz; print('bcolz', bcolz.__version__, 'blosc', ' '.join(bcolz.blosc_version()))
import dask; print('dask', dask.__version__)
import dask.array as da
from dask.diagnostics import Profiler, ResourceProfiler, CacheProfiler, visualize
from cachey import nbytes
import bokeh
from bokeh.io import output_notebook
output_notebook()
import allel
from allel.chunked.storage_hdf5 import h5fmem

numpy 1.11.0
zarr refactor blosc 1.8.1 $Date:: 2016-04-08 #$
bcolz 1.0.0 blosc 1.8.1 $Date:: 2016-04-08 #$
dask 0.8.2


Loading BokehJS ...

In [4]:
a1 = np.arange(1e8, dtype='i4')
a1

array([       0,        1,        2, ..., 99999997, 99999998, 99999999], dtype=int32)

In [5]:
a2 = np.empty_like(a1)
a2

array([0, 0, 0, ..., 0, 0, 0], dtype=int32)

In [6]:
c1 = bcolz.carray(a1, cparams=bcolz.cparams(cname='zlib', clevel=1, shuffle=1))
c1

carray((100000000,), int32)
  nbytes: 381.47 MB; cbytes: 4.66 MB; ratio: 81.88
  cparams := cparams(clevel=1, shuffle=1, cname='zlib')
[       0        1        2 ..., 99999997 99999998 99999999]

In [7]:
c2 = bcolz.zeros(c1.shape, dtype=c1.dtype, cparams=c1.cparams)
c2

carray((100000000,), int32)
  nbytes: 381.47 MB; cbytes: 1.07 MB; ratio: 356.11
  cparams := cparams(clevel=1, shuffle=1, cname='zlib')
[0 0 0 ..., 0 0 0]

In [8]:
h5f = h5fmem()
h5f

<HDF5 file "tmpbzfzvcv9" (mode r+)>

In [9]:
h1 = h5f.create_dataset('h1', data=a1, chunks=(c1.chunklen,), compression='gzip', compression_opts=1, shuffle=True)
h1

<HDF5 dataset "h1": shape (100000000,), type "<i4">

In [10]:
# get some diagnostics on compression ratio etc.
allel.chunked.ChunkedArray(h1)

ChunkedArray((100000000,), int32, nbytes=381.5M, cbytes=2.7M, cratio=142.6, cname=gzip, clevel=1, shuffle=True, chunks=(262144,), data=h5py._hl.dataset.Dataset)

In [11]:
h2 = h5f.require_dataset('h2', shape=a1.shape, dtype=a1.dtype, chunks=h1.chunks, compression=h1.compression, compression_opts=h1.compression_opts, shuffle=h1.shuffle)
h2

<HDF5 dataset "h2": shape (100000000,), type "<i4">

In [13]:
z1 = zarr.array(a1, chunks=c1.chunklen, cname='zlib', clevel=1, shuffle=1, synchronizer=zarr.ThreadSynchronizer())
z1

zarr.array.SynchronizedArray((100000000,), int32, chunks=(262144,))
  cname: zlib; clevel: 1; shuffle: 1 (BYTESHUFFLE)
  nbytes: 381.5M; cbytes: 3.6M; ratio: 105.4; initialized: 382/382
  store: zarr.store.memory.MemoryStore
  synchronizer: zarr.sync.ThreadSynchronizer

In [14]:
z2 = zarr.empty(z1.shape, chunks=z1.chunks, dtype=z1.dtype, 
                cname=z1.cname, clevel=z1.clevel, shuffle=z1.shuffle,
                synchronizer=zarr.ThreadSynchronizer())
z2

zarr.array.SynchronizedArray((100000000,), int32, chunks=(262144,))
  cname: zlib; clevel: 1; shuffle: 1 (BYTESHUFFLE)
  nbytes: 381.5M; cbytes: 0; initialized: 0/382
  store: zarr.store.memory.MemoryStore
  synchronizer: zarr.sync.ThreadSynchronizer

In [15]:
def chunked_copy(source, dest, chunklen):
    for i in range(0, source.shape[0], chunklen):
        dest[i:i+chunklen] = source[i:i+chunklen]
        

In [23]:
def dask_copy(source, dest, chunks, num_workers=2):
    x = da.from_array(source, chunks=chunks, name='source')
    da.store(x, dest, num_workers=num_workers)

In [21]:
%time a2[:] = a1

CPU times: user 84 ms, sys: 4 ms, total: 88 ms
Wall time: 84.9 ms


In [24]:
%time chunked_copy(a1, a2, c1.chunklen)
%time dask_copy(a1, a2, c1.chunklen, num_workers=1)

CPU times: user 68 ms, sys: 0 ns, total: 68 ms
Wall time: 69.1 ms
CPU times: user 252 ms, sys: 12 ms, total: 264 ms
Wall time: 252 ms


In [25]:
%time chunked_copy(h1, h2, h1.chunks[0])
%time dask_copy(h1, h2, h1.chunks)

CPU times: user 2.43 s, sys: 112 ms, total: 2.54 s
Wall time: 2.54 s
CPU times: user 4.87 s, sys: 384 ms, total: 5.25 s
Wall time: 5.15 s


In [26]:
bcolz.blosc_set_nthreads(1)
%time chunked_copy(c1, c2, c1.chunklen)
%time dask_copy(c1, c2, c1.chunklen)

CPU times: user 1.31 s, sys: 8 ms, total: 1.32 s
Wall time: 1.31 s
CPU times: user 2.94 s, sys: 264 ms, total: 3.2 s
Wall time: 3.12 s


In [33]:
bcolz.blosc_set_nthreads(2)
%time chunked_copy(c1, c2, c1.chunklen)

CPU times: user 1.74 s, sys: 424 ms, total: 2.17 s
Wall time: 1.16 s


In [29]:
%time chunked_copy(h1, h2, c1.chunklen)

CPU times: user 2.6 s, sys: 132 ms, total: 2.73 s
Wall time: 2.72 s


In [32]:
zarr.set_blosc_options(use_context=False, nthreads=2)
%time chunked_copy(z1, z2, c1.chunklen)

CPU times: user 1.74 s, sys: 360 ms, total: 2.1 s
Wall time: 1.12 s


In [34]:
%time da.from_array(a1, chunks=c1.chunklen).store(a2, num_workers=2)

CPU times: user 956 ms, sys: 20 ms, total: 976 ms
Wall time: 892 ms


In [35]:
%time da.from_array(h1, chunks=h1.chunks).store(h2, num_workers=2)

CPU times: user 3.51 s, sys: 464 ms, total: 3.97 s
Wall time: 3.9 s


In [36]:
bcolz.blosc_set_nthreads(1)
%time da.from_array(c1, chunks=c1.chunklen).store(c2, num_workers=2)

CPU times: user 2.7 s, sys: 384 ms, total: 3.08 s
Wall time: 3 s


In [37]:
bcolz.blosc_set_nthreads(2)
%time da.from_array(c1, chunks=c1.chunklen).store(c2, num_workers=2)

CPU times: user 1.7 s, sys: 432 ms, total: 2.14 s
Wall time: 1.2 s


In [38]:
%time da.from_array(z1, chunks=z1.chunks).store(z2, num_workers=2)

CPU times: user 1.96 s, sys: 204 ms, total: 2.17 s
Wall time: 1.34 s


In [39]:
def profile_copy(xd, dest, num_workers=2, dt=0.01):
    
    with Profiler() as prof, ResourceProfiler(dt=dt) as rprof:
        xd.store(dest, num_workers=num_workers)

    visualize([prof, rprof], )

In [40]:
profile_copy(da.from_array(a1, chunks=c1.chunklen), a2)

In [41]:
profile_copy(da.from_array(h1, chunks=h1.chunks), h2)

In [42]:
bcolz.blosc_set_nthreads(1)
profile_copy(da.from_array(c1, chunks=c1.chunklen), c2)

In [43]:
bcolz.blosc_set_nthreads(2)
profile_copy(da.from_array(c1, chunks=c1.chunklen), c2)

In [44]:
zarr.set_blosc_options(use_context=True)
profile_copy(da.from_array(z1, chunks=z1.chunks), z2)

In [45]:
def chunked_compute_1d(f, source, dest, chunklen):
    for i in range(0, source.shape[0], chunklen):
        dest[i:i+chunklen] = f(source[i:i+chunklen])
        

In [46]:
def dask_compute(f, source, dest, chunks, num_workers=2):
    x = da.from_array(source, chunks=chunks)
    y = f(x)
    y.store(dest, num_workers=num_workers)

In [91]:
%time chunked_copy_1d(a1, a2, c1.chunklen)
%time chunked_compute_1d(lambda x: x ** 2, a1, a2, c1.chunklen)
%time dask_compute(lambda x: x ** 2, a1, a2, c1.chunklen)

CPU times: user 72 ms, sys: 4 ms, total: 76 ms
Wall time: 72.2 ms
CPU times: user 108 ms, sys: 0 ns, total: 108 ms
Wall time: 105 ms
CPU times: user 988 ms, sys: 76 ms, total: 1.06 s
Wall time: 934 ms


In [92]:
%time chunked_copy_1d(h1, h2, c1.chunklen)
%time chunked_compute_1d(lambda x: x ** 2, h1, h2, c1.chunklen)
%time dask_compute(lambda x: x ** 2, h1, h2, h1.chunks)

CPU times: user 2.65 s, sys: 8 ms, total: 2.66 s
Wall time: 2.63 s
CPU times: user 7.12 s, sys: 120 ms, total: 7.24 s
Wall time: 7.14 s
CPU times: user 13.5 s, sys: 848 ms, total: 14.4 s
Wall time: 13.8 s


In [93]:
bcolz.blosc_set_nthreads(1)
%time chunked_copy_1d(c1, c2, c1.chunklen)
%time chunked_compute_1d(lambda x: x ** 2, c1, c2, c1.chunklen)
%time dask_compute(lambda x: x ** 2, c1, c2, c1.chunklen)

CPU times: user 1.37 s, sys: 8 ms, total: 1.38 s
Wall time: 1.36 s
CPU times: user 5.46 s, sys: 44 ms, total: 5.5 s
Wall time: 5.44 s
CPU times: user 10.9 s, sys: 632 ms, total: 11.6 s
Wall time: 11 s


In [94]:
bcolz.blosc_set_nthreads(2)
%time chunked_copy_1d(c1, c2, c1.chunklen)
%time chunked_compute_1d(lambda x: x ** 2, c1, c2, c1.chunklen)
%time dask_compute(lambda x: x ** 2, c1, c2, c1.chunklen)

CPU times: user 1.58 s, sys: 16 ms, total: 1.6 s
Wall time: 830 ms
CPU times: user 5.69 s, sys: 36 ms, total: 5.73 s
Wall time: 2.98 s
CPU times: user 6.44 s, sys: 240 ms, total: 6.68 s
Wall time: 3.52 s


In [95]:
%time chunked_copy_1d(z1, z2, c1.chunklen)
%time chunked_compute_1d(lambda x: x ** 2, z1, z2, c1.chunklen)
%time dask_compute(lambda x: x ** 2, z1, z2, z1.chunks)

CPU times: user 1.34 s, sys: 4 ms, total: 1.34 s
Wall time: 1.32 s
CPU times: user 4.86 s, sys: 36 ms, total: 4.9 s
Wall time: 4.81 s
CPU times: user 6.89 s, sys: 128 ms, total: 7.02 s
Wall time: 5.88 s


In [47]:
def profile_computation_1(xd, dest, num_workers=4, dt=0.1):
    
    # computation
#     yd = da.sin(xd)
    yd = xd ** 2
    
    with Profiler() as prof, ResourceProfiler(dt=dt) as rprof:
        yd.store(dest, num_workers=num_workers)

    visualize([prof, rprof])

In [48]:
profile_computation_1(da.from_array(a1, chunks=c1.chunklen), a2, dt=0.01)

In [49]:
profile_computation_1(da.from_array(h1, chunks=h1.chunks), h2)

In [50]:
bcolz.blosc_set_nthreads(1)
profile_computation_1(da.from_array(c1, chunks=c1.chunklen), c2)

In [51]:
bcolz.blosc_set_nthreads(2)
profile_computation_1(da.from_array(c1, chunks=c1.chunklen), c2)

In [52]:
zarr.set_blosc_options(use_context=True)
profile_computation_1(da.from_array(z1, chunks=z1.chunks), z2)